In [1]:
from sklearn.datasets import make_friedman2
from sklearn.gaussian_process import GaussianProcessRegressor
from sklearn.gaussian_process.kernels import DotProduct, WhiteKernel
from sklearn.gaussian_process.kernels import ConstantKernel, RBF
import pandas as pd
import numpy as np
import json
import plotly.express as px
import plotly
import plotly.graph_objects as go

In [2]:
df = pd.read_csv('modeloJoinville.csv')
df.head(5)

Unnamed: 0  request_id        lat        lon            api_id    lat_api  \
0           0           6 -26.292994 -48.849462              Here -26.364340   
1           1           6 -26.292994 -48.849462  OpenRouteService -26.292994   
2           2           6 -26.292994 -48.849462            Google -26.353314   
3           3           7 -26.352117 -48.815669            TomTom -26.352610   
4           4           7 -26.352117 -48.815669  OpenRouteService -26.352117   

     lon_api  
0 -48.828640  
1 -48.849462  
2 -48.772395  
3 -48.815200  
4 -48.815669

In [3]:
df = df.dropna()
df = df.sample(n = 200)

In [4]:
X = df[['lat', 'lon']].to_numpy()
y1 = df['lat_api'].to_numpy()
y2 = df['lon_api'].to_numpy()


In [5]:
print(np.mean(y1))
print(np.mean(y2))

-26.299171542000003
-48.84002559300001


In [6]:
regressorLat = GaussianProcessRegressor()
regressorLon = GaussianProcessRegressor()


In [7]:
regressorLat.fit(X, y1)
regressorLon.fit(X, y2)

GaussianProcessRegressor()

In [8]:
r1 = regressorLat.predict(X,return_std=True,return_cov=False)
r2 = regressorLon.predict(X,return_std=True,return_cov=False)

t1 = r1[0].tolist()
t2 = r2[0].tolist()

r1 = (r1[1]).tolist()
r2 = (r2[1]).tolist()


In [9]:
df['incertezaLat'] = r1
df['incertezaLon'] = r2
df['predLat'] = t1
df['predLon'] = t2

df.head(5)

Unnamed: 0  request_id        lat        lon            api_id  \
264795      264795      296010 -26.251344 -48.854094            MapBox   
371325      371325      369312 -26.276679 -48.795809  OpenRouteService   
294206      294206      313446 -26.268530 -48.807731  OpenRouteService   
565835      565835      591712 -26.292994 -48.849462  OpenRouteService   
67913        67913       78114 -26.311008 -48.877785  OpenRouteService   

          lat_api    lon_api  incertezaLat  incertezaLon    predLat    predLon  
264795 -26.252524 -48.853994      0.000004      0.000004 -26.257223 -48.854500  
371325 -26.276679 -48.795809      0.000004      0.000004 -26.277678 -48.796142  
294206 -26.268530 -48.807731      0.000002      0.000002 -26.269281 -48.807566  
565835 -26.292994 -48.849462      0.000001      0.000001 -26.290302 -48.846410  
67913  -26.311008 -48.877785      0.000003      0.000003 -26.305923 -48.874684

In [10]:
# Mapa da Incerteza da Latitude

mapa = px.scatter_mapbox(
    df, 
    lat='lat', 
    lon='lon',  
    hover_name='incertezaLat',
    color_continuous_scale='Hot',
    color='incertezaLat',                     
    zoom= 3,
    hover_data={'incertezaLat': ':.10f'},
    title='<b>Incerteza por Latitude</b>'
)
mapa.update_layout(
    mapbox_style='open-street-map',
    height=600, 
    margin={'r':0, 't':0, 'l':0, 'b':0},
    title_x=0.5,
    title_y=0.96,
)
mapa.show()

In [11]:
lat = df['lat'].to_numpy()
lon = df['lon'].to_numpy()
z = np.zeros((len(lat),len(lon)))
for i in range(len(lat)):
    for j in range(len(lon)):
        z[i][j] = regressorLat.predict([[lat[i],lon[j]]], return_std=True)[1]

In [12]:
min_lat = np.min(lat)
min_lon = np.min(lon)
max_lat = np.max(lat)
max_lon = np.max(lon)

In [13]:
lats = np.linspace(min_lat, max_lat, num = 200)
lons = np.linspace(min_lon, max_lon, num = 200)
#lats = lat
#lons = lon
z = np.zeros((len(lats),len(lons)))
for i in range(len(lats)):
    for j in range(len(lons)):
        z[i][j] = regressorLat.predict([[lats[i],lons[j]]], return_std=True)[1]

In [14]:
fig = go.Figure(data=[go.Contour(z=z, x0=min_lat, y0=min_lon, dx=np.abs(lats[0]-lats[1]), dy=np.abs(lons[0]-lons[1]),line_smoothing=0,colorscale='Hot')])
#fig.update_layout(title='Mt Bruno Elevation', autosize=False,
#                 width=500, height=500,
#                 margin=dict(l=65, r=50, b=65, t=90))
fig.show()
#mapa.add_trace(fig.data[0])
#mapa.show()
#mapa.add_trace(go.Surface(z=z, x=lats, y=lons, showscale=False))
#mapa.show()

In [15]:
# Mapa da Incerteza da Longitude

mapa = px.scatter_mapbox(
    df, 
    lat='lat', 
    lon='lon',  
    hover_name='incertezaLon',
    color_continuous_scale='Hot',
    color='incertezaLon',                     
    zoom= 3,
    hover_data={'incertezaLon': ':.10f'},
    title='<b>Incerteza por Longitude</b>'
)
mapa.update_layout(
    mapbox_style='open-street-map',
    height=600, 
    margin={'r':0, 't':0, 'l':0, 'b':0},
    title_x=0.5,
    title_y=0.96,
)
mapa.show()

In [16]:
lats = np.linspace(min_lat, max_lat, num = 200)
lons = np.linspace(min_lon, max_lon, num = 200)
#lats = lat
#lons = lon
z = np.zeros((len(lats),len(lons)))
for i in range(len(lats)):
    for j in range(len(lons)):
        z[i][j] = regressorLon.predict([[lats[i],lons[j]]], return_std=True)[1]

In [17]:
fig = go.Figure(data=[go.Contour(z=z, x0=min_lat, y0=min_lon, dx=np.abs(lats[0]-lats[1]), dy=np.abs(lons[0]-lons[1]),line_smoothing=0,colorscale='Hot')])
fig.show()